# If these install, restart the kernal so it has access to the recently installed files

In [1]:
!pip3 install --user transformers datasets evaluate rouge_score
!pip3 install --user datasets
!pip install --user transformers[torch]
!pip install --user accelerate -U
!pip install --user wandb

# Logging into huggingface hub

In [1]:
from huggingface_hub import notebook_login

notebook_login()

# Naming the WANDB project and notebook

In [2]:
# Must set the global variable WANDB_NOTEBOOK_NAME to the name of the notebook
import os
import wandb
# Name is found through the os incase the name changes
# WANDB_NOTEBOOK_NAME = os.path.basename(os.getcwd())
notebook_name = str(os.path.basename(os.getcwd()))
os.environ["WANDB_NOTEBOOK_NAME"] = "./" + notebook_name
os.environ["WANDB_PROJECT"] = "senate_bills_summary_model"
wandb.init(project='senate_bills_sumamry_model')

wandb: WARNING WANDB_NOTEBOOK_NAME should be a path to a notebook file, couldn't find ./content.
wandb: Currently logged in as: tah6k (cheaptrix). Use `wandb login --relogin` to force relogin


# Importing and loading the Congressional Bills dataset

In [3]:
import datasets
from datasets import load_dataset
import pandas as pd
from datasets import Dataset
import json

# Opening JSON file
with open("cleaned_senate_bill_sum_data.json") as json_file:
    cleaned_data = json.load(json_file)
data = pd.DataFrame.from_dict(cleaned_data)
dataset = Dataset.from_pandas(pd.DataFrame(data=data))

# Splitting the data to training and testing split

In [4]:
billsum = dataset.train_test_split(test_size=0.2)

# Example of data within the training set

In [5]:
billsum["train"][0]

{'summary': 'Improving Cooperation with States and Local Governments and Preventing the Catch and Release of Criminal Aliens Act of 2015 This bill prohibits a jurisdiction from receiving any of the funding specified in this Act if it does not cooperate with federal officials regarding criminal aliens or other aliens deemed to be a removal priority by the Department of Homeland Security (DHS), including by refusing to: (1) detain or transfer custody of such aliens pursuant to detainers placed upon them; or (2) notify a federal law enforcement agency, upon request, of their release. Such funding consists of: incarceration reimbursement funds under the Immigration and Nationality Act, grant funding under the Second Chance Act of 2007, and any other law enforcement related grants or contracts awarded by DHS or the Department of Justice (DOJ). A jurisdiction shall become eligible to receive such funds, grants, or contracts after DHS certifies that: the jurisdiction no longer fails to cooper

In [6]:
billsum["test"][0]

{'summary': 'Budgeting for Disasters Act This bill modifies the budget enforcement procedures that apply to federal spending for natural disasters and emergencies. The bill includes provisions that eliminate the requirements to adjust annual discretionary spending limits to accommodate additional appropriations for disaster relief and wildfire suppression; increase the number of votes that is required to waive the Senate point of order against emergency spending designations, which exempt spending from discretionary spending limits; and require the Government Accountability Office to report on spending for emergencies and disaster relief.',
 'text': '116 S1579 IS: Budgeting for Disasters Act U.S. Senate 2019-05-21 text/xml EN Pursuant to Title 17 Section 105 of the United States Code, this file is not subject to copyright protection and is in the public domain. II 116th CONGRESS 1st Session S. 1579 IN THE SENATE OF THE UNITED STATES May 21, 2019 Mr. Romney Mr. Lee Mr. Braun Mr. Toomey 

In [7]:
len(billsum["test"])

2619

# Load T5 tokenizer to process text and summary

In [8]:
from transformers import AutoTokenizer

checkpoint = "google-t5/t5-small"
# checkpoint = "google-t5/t5-base" # GPU too small
tokenizer = AutoTokenizer.from_pretrained(checkpoint)

/root/.local/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/root/.local/lib/python3.10/site-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


# Perprocessing Function

In [9]:
prefix = "summarize: "


def preprocess_function(examples):
    inputs = [prefix + doc for doc in examples["text"]]
    # max_length was 1024
    model_inputs = tokenizer(inputs, max_length=2048, truncation=True)

    # max_length was 128
    labels = tokenizer(text_target=examples["summary"], max_length=256, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

# Tokenize the dataset using the map function

In [10]:
tokenized_billsum = billsum.map(preprocess_function, batched=True)

Map:   0%|          | 0/10474 [00:00<?, ? examples/s]

Map:   0%|          | 0/2619 [00:00<?, ? examples/s]

# Creating a batch of examples using DataCollatorForSeq2Seq with dynamic padding

In [11]:
from transformers import DataCollatorForSeq2Seq

data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=checkpoint)

# Importing the evaluator

In [12]:
import evaluate

rouge = evaluate.load("rouge")

# Function that passes predictions and labels to compute to calculate the Rouge metric.

In [13]:
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    decoded_preds = tokenizer.batch_decode(predictions, skip_special_tokens=True)
    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)

    result = rouge.compute(predictions=decoded_preds, references=decoded_labels, use_stemmer=True)

    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in predictions]
    result["gen_len"] = np.mean(prediction_lens)

    return {k: round(v, 4) for k, v in result.items()}

# Training - Loading T5 with AutoModelForSeq2SeqLM

In [14]:
from transformers import AutoModelForSeq2SeqLM, Seq2SeqTrainingArguments, Seq2SeqTrainer

model = AutoModelForSeq2SeqLM.from_pretrained(checkpoint)

/root/.local/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


# Defining the training hyperparameters

In [21]:
# ORIGINAL
# training_args = Seq2SeqTrainingArguments(
#     output_dir="my_awesome_billsum_model",
#     evaluation_strategy="epoch",
#     learning_rate=2e-5,
#     per_device_train_batch_size=16,
#     per_device_eval_batch_size=16,
#     weight_decay=0.01,
#     save_total_limit=3,
#     num_train_epochs=4,
#     predict_with_generate=True,
#     fp16=True,
#     push_to_hub=True,
# )

training_args = Seq2SeqTrainingArguments(
    output_dir="senate_bills_summary_model",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=14,
    per_device_eval_batch_size=14,
    weight_decay=0.01,
    save_total_limit=3,
    num_train_epochs=4,
    predict_with_generate=True,
    fp16=True,
    push_to_hub=True,
)

# Passing the arguments, model, dataset, tokenizer, data collator, and compute_metrics function to Seq2SeqTrainer for training

In [22]:
trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_billsum["train"],
    eval_dataset=tokenized_billsum["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

# Fine-tuning the model

In [23]:
# Training needs numpy
import numpy as np

# Fine-tuning the model
trainer.train()

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1141: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1141: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1141: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1141: UserWarning: Using the model-agnostic default `max_length` (=20) to control

TrainOutput(global_step=2996, training_loss=2.152087345301548, metrics={'train_runtime': 2020.1845, 'train_samples_per_second': 20.739, 'train_steps_per_second': 1.483, 'total_flos': 2.2664040428273664e+16, 'train_loss': 2.152087345301548, 'epoch': 4.0})

# Saving the Model

In [24]:
trainer.save_model("./senate_bills_summary_model")

Upload 2 LFS files:   0%|          | 0/2 [00:00<?, ?it/s]

events.out.tfevents.1715052376.7c3b2edd5873.9866.2:   0%|          | 0.00/9.24k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/242M [00:00<?, ?B/s]

# Pushing Model to Personal HuggingFace Hub

In [25]:
trainer.push_to_hub("cheaptrix/senate_bills_summary_model")

CommitInfo(commit_url='https://huggingface.co/cheaptrix/senate_bills_summary_model/commit/cb7e3340639e86fb27921607f266b604a8f8384c', commit_message='cheaptrix/senate_bills_summary_model', commit_description='', oid='cb7e3340639e86fb27921607f266b604a8f8384c', pr_url=None, pr_revision=None, pr_num=None)

# Interface

In [36]:
# Send some of the test set through using a list of dictionaries
cleaned_test_data = list(billsum["test"])[:20]

In [38]:
len(cleaned_test_data)

20

In [ ]:
# cleaned_test_data = []
# # Opening JSON file
# with open("cleaned_bill_sum_test_data.json") as json_file:
#     cleaned_test_data = json.load(json_file)

# Creating a pipeline with the transformers module

In [40]:
from transformers import pipeline

summarizer = pipeline("summarization", model="cheaptrix/senate_bills_summary_model")

/root/.local/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


config.json:   0%|          | 0.00/1.51k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/242M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/20.7k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.42M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.54k [00:00<?, ?B/s]

In [41]:
generated_summaries = []
for i in range(len(cleaned_test_data)):
    summary = summarizer(cleaned_test_data[i]['text'])
    generated_summaries.append({"generated" : summary[0]['summary_text'], "summary" : cleaned_test_data[i]['summary']})

Token indices sequence length is longer than the specified maximum sequence length for this model (692 > 512). Running this sequence through the model will result in indexing errors


In [42]:
generated_summaries[0]

{'generated': 'Budgeting for Disasters Act This bill requires the Comptroller General of the United States to submit to Congress a report that reviews and reviews amounts appropriated for each of fiscal years 2009 through 2018 that were designated as being for an emergency requirement, or made available to provide assistance under the Robert T. Stafford Disaster Relief and Emergency Assistance Act (RDA). The bill also requires the Department of the Treasury (GAO) to report to Congress that: (1) reviews amounts designated for each fiscal year 2009 through 2018, and (3) provide recommendations to: clarify the definition of emergency requirements for purposes of appropriated amounts being designated as a major disaster requirement; and (3) improve cost-sharing relating to major disasters and emergencies among federal, state, and local governments; and improve forecasting and budgeting for appropriations for disaster relief.',
 'summary': 'Budgeting for Disasters Act This bill modifies the

In [43]:
generated_summaries[1]

{'generated': 'Motorcyclist Advisory Council Reauthorization Act This bill amends the FAST Act to amend a provision relating to the Council. The Council shall be comprised of 12 members, to be appointed by the Secretary, of whom five shall be representatives of units of state or local government with expertise pertaining to highway engineering and safety issues, including: barrier design; road design, construction, and maintenance; or intelligent transportation systems; one shall be a motorcyclist who serves as a traffic and safety engineer; design engineer; or other transportation department official; a roadway safety data expert with expertise in crash testing and analysis; and the architecture and implementation of intelligent transportation system technologies.',
 'summary': "Motorcyclist Advisory Council Reauthorization Act This bill amends Fixing America's Surface Transportation Act or the FAST Act to provide statutory authority for the establishment of a Motorcyclist Advisory Co

In [44]:
generated_summaries[2]

{'generated': "Ensuring Kids Have Access to Medically Necessary Dental Care Act This bill amends title XXI of the Social Security Act to prohibit lifetime or annual limits on dental benefits for certain children under the Children's Health Insurance Program. Specifically, the bill prohibits states from establishing lifetime or year limits on the dollar value of benefits for dental services provided under the child health plan to a targeted low-income child and, in the case that the state elects to provide pregnancy-related assistance, to an underage pregnant woman, including benefits for such services that are provided through dental coverage otherwise equivalent to benchmark dental package.",
 'summary': "Ensuring Kids Have Access to Medically Necessary Dental Care Act This bill modifies dental coverage under the Children's Health Insurance Program (CHIP). Specifically, the bill prohibits lifetime or annual limits on CHIP dental coverage. It also requires states to offer dental-only s

In [45]:
generated_summaries[3]

{'generated': "Preventing Crimes Against Veterans Act of 2019 This bill amends title 18, the United States Code, to provide an additional tool to prevent certain frauds against veterans. It shall be unlawful for any person to knowingly engage in any scheme or artifice to defraud (1) an individual of veterans' benefits; or (2) in connection with obtaining veteran's benefits for an individual.",
 'summary': "Preventing Crimes Against Veterans Act of 2019 This bill establishes a new criminal offense for knowingly engaging in a scheme to defraud an individual of veterans' benefits, or in connection with obtaining veteran's benefits for an individual. A violator is subject to criminal penalties&#8212;a fine, a prison term of up to five years, or both."}

In [46]:
generated_summaries[4]

{'generated': 'Grandfamilies Act of 2019 This bill directs the Department of Health and Human Services (HHS) to establish a National Technical Assistance Center on GrandFamilies to provide grants to owners of grandfamily housing for grandfamily resident service coordinators to support housing programming services, equipment, and building structures. Specifically, HHS must reduce the grant payable to HHS for the immediately succeeding fiscal year by an amount equal to 3 percent of the state family assistance grant. HHS shall also issue guidance to states on ways to ensure that kinship caregivers are eligible for assistance under the program. The bill prohibits a state from requiring an individual to engage in work if the individual fails to satisfy the cooperation requirement.',
 'summary': 'Grandfamilies Act of 2019 This bill expands access to specified programs for children living with grandparents or other family members who are not their legal guardian. Specifically, the bill provid

In [47]:
generated_summaries[5]

{'generated': 'Racehorse Doping Ban Act of 2019 This bill establishes an independent anti-doping organization with responsibility for ensuring the integrity and safety of horseraces that are the subject of interstate off-track wagers. Specifically, a host racing association may conduct a horserace that is subject to an interstate on-track betting, and a non-transfer rule with respect to furosemide is within the context of a veterinarian-client-patient relationship.',
 'summary': "Racehorse Doping Ban Act of 2019 This bill requires that there be an independent anti-doping organization with responsibility for ensuring the integrity and safety of horse races that are the subject of interstate off-track wagers. The bill prescribes conditions under which such organization may (1) suspend the period a person is excluded from participation, and (2) permit the use of furosemide in a horse participating in such a race during the two-year period following this bill's enactment. A host racing ass

In [48]:
generated_summaries[6]

{'generated': 'Small Business Tax Compliance Relief Act of 2015 This bill amends the Internal Revenue Code to allow small business taxpayers to use inventories for any taxable year, but the taxpayer meets the gross receipts test of the de minimis safe harbor for taxpayers without applicable financial statements from $500 to $2,500, requiring adequate records showing the dollar amount being expensed in lieu of accounting procedures in place at the beginning of the year, and modifying the definition of applicable financial statement to include reviewed financial statements. Requires the Secretary of the Treasury to waive any penalty or addition to tax for failure to report certain transactions. The bill also amends rules for nonqualified deferred compensation plans.',
 'summary': 'Small Business Tax Compliance Relief Act of 2015 This bill amends provisions of the the Internal Revenue Code relating to the taxation of small businesses to: allow small business entities with gross receipts n

In [49]:
generated_summaries[7]

{'generated': 'Improving Broadband Access for Veterans Act of 2017 This bill requires the Federal Communications Commission (FCC) to submit to Congress a report on promoting broadband Internet access service for veterans, in particular low-income veterans and veterans residing in rural areas, and how to promote broadband internet access service.',
 'summary': 'Improving Broadband Access for Veterans Act of 2017 This bill requires the Federal Communications Commission (FCC) to submit to Congress a report on promoting broadband Internet access service for veterans, in particular low-income veterans and veterans residing in rural areas. In preparing the report, the FCC shall provide the public with notice and an opportunity to comment.'}

In [50]:
generated_summaries[8]

{'generated': 'Charles Duncan Buried with Honor Act of 2016 This bill authorizes the Department of Veterans Affairs (VA) to furnish caskets and urns for burial of certain veterans in cemeteries of states and tribal organizations of veterans without next of kin or sufficient resources to provide for them.',
 'summary': "(This measure has not been amended since it was passed by the Senate on September 20, 2016. The summary of that version is repeated here.) Charles Duncan Buried with Honor Act of 2016 (Sec. 2) This bill authorizes the Department of Veterans Affairs (VA), if it is unable to identify a deceased veteran's next of kin and if it determines that sufficient resources for the furnishing of a casket or urn for the burial of such veteran are not otherwise available, to furnish a casket or urn for the burial of such veteran in a national cemetery (current law) or in a veterans cemetery of a state or tribal organization for which the VA has provided a grant for the establishment, ex

In [51]:
generated_summaries[9]

{'generated': 'Abortion Non-Discrimination Act of 2015 This bill amends the Public Health Service Act to prohibit certain abortion-related discrimination in governmental activities.',
 'summary': 'Abortion Non-Discrimination Act of 2015 Amends the Public Health Service Act to prohibit the federal government and any state or local government receiving federal financial assistance from subjecting an institutional or individual health care entity, including any health professional, facility, organization, or insurance plan, to discrimination on the basis that the entity refuses to participate in abortion-related activities. Creates a cause of action for any violation of the abortion discrimination prohibition. Gives federal courts jurisdiction to prevent and redress actual or threatened violations by issuing legal or equitable relief, including injunctions and orders preventing the disbursement of all or a portion of federal financial assistance until the prohibited conduct has ceased. Gi

In [52]:
generated_summaries[10]

{'generated': 'Small Business Growth Act This bill amends the Internal Revenue Code to increase the dollar limitation for the election to expense certain depreciable business assets.',
 'summary': 'Small Business Growth Act This bill increases from $1 million to $2.5 million the limitation on expensing of depreciable business assets. It also increases the asset threshold amount used to reduce the expensing limitation.'}

In [53]:
generated_summaries[11]

{'generated': 'Building Solutions for Veterans Experiencing Homelessness Act of 2021 This bill requires the Department of Veterans Affairs (VA) to establish and carry out a pilot program to assess the feasibility and advisability of awarding grants to eligible entities for the provision or coordination of recovery services for substance use disorder or alcohol use disorder for veterans who were previously homeless and are transitioning to permanent housing and veterans who are at risk of becoming homeless.',
 'summary': 'Building Solutions for Veterans Experiencing Homelessness Act of 2021 This bill addresses various Department of Veterans Affairs (VA) grants, programs, and assistance related to services for homeless veterans. The bill removes certain funding limitations on grants that assist eligible entities in establishing or modifying programs to furnish outreach, rehabilitative services, vocational counseling and training, and transitional housing assistance to homeless veterans. 

In [54]:
generated_summaries[12]

{'generated': 'LGBT Elder Americans Act of 2017 This bill directs the Department of Health and Human Services (HHS) to establish and operate the National Resource Center on Lesbian, Gay, Bisexual, and Transgen\xadder Aging. The Center shall provide national, state, and local organizations, including those with a primary mission of serving LGBT individuals, with the information and technical assistance the organizations need to effectively serve LGBT older individuals. Specifically, the Center shall have three primary objectives, consisting of: educating aging services organizations about the existence and special needs of older individuals; and providing educational resources to LGBT elders and their caregivers.',
 'summary': 'LGBT Elder Americans Act of 2017 This bill amends the Older Americans Act of 1965 to include the specific needs of&nbsp;lesbian, gay, bisexual, and transgender (LGBT) individuals among the "greatest social needs" served under that Act. An LGBT individual shall be

In [55]:
generated_summaries[13]

{'generated': 'Main Street Employee Ownership Act of 2018 This bill expands opportunities to available employee-owned business concerns through Small Business Administration loan programs. The bill establishes a small business microloan program to offer technical assistance and training on the transition to employee ownership through cooperatives and qualified employee trusts. The program shall provide outreach and educational materials to companies licensed under the Small Business Investment Act of 1958 to provide access to information and resources on employee ownership via cooperatives or qualified employees as a business succession strategy, conduct training and educational activities, and carry out the activities of a cooperative.',
 'summary': "Main Street Employee Ownership Act of 2018 This bill amends the Small Business Act to expand the authority of the Small Business Administration (SBA) to guarantee loans for qualified employee trusts of a small business to purchase the sto

In [56]:
generated_summaries[14]

{'generated': "Rhode Island Fishermen's Fairness Act of 2017 This bill amends the Magnuson-Stevens Fishery Conservation and Management Act to add Rhode Island to the Mid-Atlantic Fishery Management Council.",
 'summary': "Rhode Island Fishermen's Fairness Act of 2017 This bill amends the Magnuson-Stevens Fishery Conservation and Management Act to add Rhode Island to the Mid-Atlantic Fishery Management Council and increase Council membership from 21 to 23 members. The Council is not given authority over the fisheries in the Atlantic Ocean seaward of Rhode Island."}

In [57]:
generated_summaries[15]

{'generated': 'Chronic Disease Management Act of 2019 This bill allows health savings account-eligible high-deductible health plans to cover chronic disease prevention and treatment on a pre-deductible basis to promote the concept of Value-Based Insurance Design, which is an effective tool to improve the quality and reduce the cost of care for Americans with chronic diseases.',
 'summary': 'Chronic Disease Management Act of 2019 This bill amends the Internal Revenue Code, with respect to health savings accounts (HSAs), to allow the high deductible health plans required for an HSA to provide care for chronic conditions with no deductible.'}

In [58]:
generated_summaries[16]

{'generated': 'Facilitating Main Street Offerings Act This bill amends the Securities Act of 1933 to define secondary offerings of Regulation A tier 2 securities as covered securities for purposes of an exemption from state regulation.',
 'summary': 'Facilitating Main Street Offerings Act This bill exempts certain securities issued under Regulation A from state regulation of secondary transactions. Regulation A exempts small issues of securities from registration requirements.'}

In [59]:
generated_summaries[17]

{'generated': 'Veterans Medical Mileage Adjustment Act of 2022 This bill amends title 38, United States Code, to increase the rate for allowances based on mileage for beneficiary travel.',
 'summary': 'Veterans Medical Mileage Adjustment Act of 2022 This bill increases the rate for beneficiary travel allowances based on mileage (from 41.5 cents to 45.5 cents per mile) for beneficiary travel to or from Department of Veterans Affairs facilities in connection with vocational rehabilitation, required counseling, or for the purpose of examination, treatment, or care.'}

In [60]:
generated_summaries[18]

{'generated': 'Platte River Recovery Implementation Program Extension Act This bill authorizes the Department of the Interior, acting through the Commissioner of Reclamation and in partnership with the States, other federal agencies, and other non-Federal entities, to continue the cooperative effort among the federal and non-federals entities through the continued implementation of the Platte river recovery implementation program First Increment Extension for threatened and endangered species in the Central and Lower Platte- River Basin, without creating federal water rights or requiring the grant of water rights to federal entities.',
 'summary': "Platte River Recovery Implementation Program Extension Act This bill revises the Platte River Recovery Implementation Program. The program is a cooperative agreement among Colorado, Wyoming, Nebraska, and the Bureau of Reclamation to protect endangered and threatened species and their habitats in the Central and Lower Platte River Basin. The

In [61]:
generated_summaries[19]

{'generated': 'Court Legal Access and Student Support (CLASS) Act of 2015 This bill prohibits the institution of higher education from requiring any student to agree to, and will not enforce, any limitation or restriction (including a limitation on any available choice of applicable law, a jury trial, or venue) on the ability of a student to pursue a claim against an institution in court.',
 'summary': "Court Legal Access and Student Support (CLASS) Act of 2015 This bill makes procedures for the enforcement of arbitration agreements inapplicable to an enrollment agreement between a student and an institution of higher education (IHE). The bill also amends the Higher Education Act of 1965 to forbid an IHE that participates in federal student aid programs, including work-study programs, from requiring a student to agree to any restriction on the student's ability to pursue a claim, individually or with others, against it in court."}

In [63]:
# Convert and write JSON object to file
with open("cleaned_test_data_output.json", "w") as outfile:
    json.dump(generated_summaries, outfile)